In [1]:
from metadrive.envs.metadrive_env import MetaDriveEnv
from metadrive.manager.traffic_manager import PGTrafficManager
from metadrive.manager.pg_map_manager import PGMapManager
from metadrive.utils.config import Config

# from metadrive.examples.ppo_expert.torch_expert import torch_expert as expert
from metadrive.examples.ppo_expert.numpy_expert import expert
from metadrive.component.map.base_map import BaseMap
from metadrive.component.map.pg_map import MapGenerateMethod
from metadrive.engine.logger import get_logger, set_log_level

import logging
import mediapy
from utils.scenario_runner import ScenarioRunner
from pathlib import Path
import numpy as np

log = get_logger()

In [2]:
def get_default_config(dr=1, dt=0.02, seed=0) -> dict:

    # ===== Termination Scheme =====
    termination_sceme = dict(
        out_of_route_done=False,
        on_continuous_line_done=False,
        crash_vehicle_done=False,
        crash_object_done=False,
        crash_human_done=False,
    )
    # ===== Map Config =====
    map_config = {
        BaseMap.GENERATE_TYPE: MapGenerateMethod.BIG_BLOCK_NUM,
        BaseMap.GENERATE_CONFIG: 5,  # 20 block
    }

    return dict(
        # use_render=True,
        log_level=logging.DEBUG,  # logging.DEBUG
        traffic_density=0.01,
        traffic_mode="respawn",
        random_traffic=False,
        map_config=map_config,
        **termination_sceme,
        decision_repeat=dr,
        physics_world_step_size=dt,
        start_seed=seed,
    )

In [3]:
env = MetaDriveEnv(config=get_default_config(dt=1 / 50))

[INFO] Environment: MetaDriveEnv
[INFO] MetaDrive version: 0.4.3
[INFO] Sensors: [lidar: Lidar(), side_detector: SideDetector(), lane_line_detector: LaneLineDetector()]
[INFO] Render Mode: none
[INFO] Horizon (Max steps per agent): None


In [4]:
_, reset_info = env.reset()

[INFO] Assets version: 0.4.3
[INFO] Known Pipes: glxGraphicsPipe
[DEBUG] Load Vehicle Module: Lidar (distance_detector.py:114)
[DEBUG] Load Vehicle Module: SideDetector (distance_detector.py:114)
[DEBUG] Load Vehicle Module: LaneLineDetector (distance_detector.py:114)
[INFO] Start Scenario Index: 0, Num Scenarios : 1
[DEBUG] FirstPGBlock is attached to the world. (base_object.py:233)
[DEBUG] Curve is attached to the world. (base_object.py:233)
[DEBUG] Curve is attached to the world. (base_object.py:233)
[DEBUG] Curve is attached to the world. (base_object.py:233)
[DEBUG] StdInterSection is attached to the world. (base_object.py:233)
[DEBUG] Curve is attached to the world. (base_object.py:233)
[DEBUG] Curve is detached from the world. (base_object.py:251)
[DEBUG] Curve is attached to the world. (base_object.py:233)
[DEBUG] Curve is detached from the world. (base_object.py:251)
[DEBUG] Curve is attached to the world. (base_object.py:233)
[DEBUG] FirstPGBlock is detached from the world. (

In [5]:
env_dt, env_dr = env.config["physics_world_step_size"], env.config["decision_repeat"]
world_fps = 1 / (env_dt * env_dr)
log.info(f"World FPS: {world_fps}")

[INFO] World FPS: 50.0


In [6]:
action = expert(env.agent, deterministic=True)
obs, reward, terminated, truncated, info = env.step(action)

[INFO] Torch is not available. Use numpy PPO expert.


In [7]:
env.close()

[DEBUG] FirstPGBlock is detached from the world. (base_object.py:251)
[DEBUG] Curve is detached from the world. (base_object.py:251)
[DEBUG] Curve is detached from the world. (base_object.py:251)
[DEBUG] Curve is detached from the world. (base_object.py:251)
[DEBUG] StdInterSection is detached from the world. (base_object.py:251)
[DEBUG] Curve is detached from the world. (base_object.py:251)
[DEBUG] Object FirstPGBlock is already detached from the world. Can not detach again (base_object.py:253)
[DEBUG] Object Curve is already detached from the world. Can not detach again (base_object.py:253)
[DEBUG] Object Curve is already detached from the world. Can not detach again (base_object.py:253)
[DEBUG] Object Curve is already detached from the world. Can not detach again (base_object.py:253)
[DEBUG] Object StdInterSection is already detached from the world. Can not detach again (base_object.py:253)
[DEBUG] Object Curve is already detached from the world. Can not detach again (base_object.py

In [8]:
def get_frame(env):
    b_box = env.current_map.road_network.get_bounding_box()
    x_len, y_len = b_box[1] - b_box[0], b_box[3] - b_box[2]

    scaling = 3
    return env.render(
        mode="topdown",
        window=False,
        screen_size=(x_len * scaling * 1.05, y_len * scaling * 1.05),
        camera_position=env.current_map.get_center_point(),
        scaling=scaling,
        draw_contour=True,
        num_stack=1,
    )

In [9]:
def get_max_steps(env: MetaDriveEnv, fps: int) -> int:
    """
    Return maximum number of simulation steps.

    Assume minimal target velocity e.g. 2m/s.
    Dependant on the total route length.
    Adaptable to fidelity parameters.
    """

    distance = env.agent.navigation.total_length
    V_min = 2.0  # [m/s]  # set minimal velocity to 2m/s
    max_time = distance / V_min  # [s] maximum time allowed to reach the destination
    max_steps = round(max_time * fps)  # maximum number of simulation steps frames

    log.info(f"Calculating max steps with: ")
    log.info(f"{V_min = }, {distance = }, {max_time = }, {fps = } {max_steps = }")

    return max_steps

In [10]:
import time


def get_frames(ads_fps=10, world_fps=60):
    env = MetaDriveEnv(config=get_default_config(dt=1 / world_fps, seed=0))
    env.reset()
    assert world_fps % ads_fps == 0, "ADS FPS must be a multiple of worlds FPS"
    assert env.config["decision_repeat"] == 1, "Decision repeat must be 1"
    frames = []
    skip_rate = world_fps // ads_fps
    log.info(f"World FPS: {world_fps}, ADS FPS: {ads_fps}, Ratio: {skip_rate}")

    timings = {"agent": 0}
    scenario_start = time.perf_counter()

    for step_no in range(get_max_steps(env, world_fps)):
        log.debug(f"Step {step_no}")
        if step_no % skip_rate == 0:
            log.debug(f"Getting agent's action")
            agent_start = time.perf_counter()
            action = expert(env.agent, deterministic=True)
            timings["agent"] += time.perf_counter() - agent_start

        obs, reward, terminated, truncated, info = env.step(action)

        if step_no % 6 == 0:
            frames.append(get_frame(env))

        if terminated or truncated:
            break
    timings["scenario"] = time.perf_counter() - scenario_start

    env.close()
    return frames, timings

In [11]:
clips = []
timings = {}

for fps in [10, 20, 30, 60]:
    scenario_frames, scenario_timings = get_frames(fps)
    clips.append(scenario_frames)
    timings[f"{fps} FPS"] = scenario_timings

[INFO] Environment: MetaDriveEnv
[INFO] MetaDrive version: 0.4.3
[INFO] Sensors: [lidar: Lidar(), side_detector: SideDetector(), lane_line_detector: LaneLineDetector()]
[INFO] Render Mode: none
[INFO] Horizon (Max steps per agent): None
[INFO] Assets version: 0.4.3
[INFO] Known Pipes: glxGraphicsPipe
[DEBUG] Load Vehicle Module: Lidar (distance_detector.py:114)
[DEBUG] Load Vehicle Module: SideDetector (distance_detector.py:114)
[DEBUG] Load Vehicle Module: LaneLineDetector (distance_detector.py:114)
[INFO] Start Scenario Index: 0, Num Scenarios : 1
[DEBUG] FirstPGBlock is attached to the world. (base_object.py:233)
[DEBUG] Curve is attached to the world. (base_object.py:233)
[DEBUG] Curve is attached to the world. (base_object.py:233)
[DEBUG] Curve is attached to the world. (base_object.py:233)
[DEBUG] StdInterSection is attached to the world. (base_object.py:233)
[DEBUG] Curve is attached to the world. (base_object.py:233)
[DEBUG] Curve is detached from the world. (base_object.py:251

In [12]:
mediapy.set_show_save_dir("data")

mediapy.show_videos(clips, titles=list(timings.keys()), fps=10)

10 FPS This browser does not support the video tag.,20 FPS This browser does not support the video tag.,30 FPS This browser does not support the video tag.,60 FPS This browser does not support the video tag.


In [13]:
timings

{'10 FPS': {'agent': 4.14984047298276, 'scenario': 35.74586046300101},
 '20 FPS': {'agent': 8.380229022010099, 'scenario': 44.621738931000436},
 '30 FPS': {'agent': 12.746307186054764, 'scenario': 50.90528500900109},
 '60 FPS': {'agent': 25.80701058588602, 'scenario': 65.80417653699988}}